In [1]:
#pip install scrapy

In [2]:
#pip install scrapy-fake-useragent

In [3]:
import logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

In [4]:
import json

class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('reviewresult.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item
    
from datetime import datetime, date

import time

import re

import scrapy

from scrapy.loader import ItemLoader
from scrapy.loader.processors import Compose, Join, MapCompose, TakeFirst
from scrapy.http import FormRequest, Request
from w3lib.url import url_query_parameter

In [5]:
class StripText:
    def __init__(self, chars=' \r\t\n'):
        self.chars = chars

    def __call__(self, value):
        try:
            return value.strip(self.chars)
        except:  
            return value
        
def str_to_float(x):
    x = x.replace(',', '')
    try:
        return float(x)
    except:  
        return x

def str_to_int(x):
    try:
        return int(str_to_float(x))
    except:  
        return x
    
def simplify_recommended(x):
    return True if x == 'Recommended' else False

def standardize_date(x):
    """
    Convert x from recognized input formats to desired output format,
    or leave unchanged if input format is not recognized.
    """
    fmt_fail = False

    for fmt in ['%b %d, %Y', '%B %d, %Y']:
        try:
            return datetime.strptime(x, fmt).strftime('%Y-%m-%d')
        except ValueError:
            fmt_fail = True

    # Induce year to current year if it is missing.
    for fmt in ['%b %d', '%B %d']:
        try:
            d = datetime.strptime(x, fmt)
            d = d.replace(year=date.today().year)
            return d.strftime('%Y-%m-%d')
        except ValueError:
            fmt_fail = True

    if fmt_fail:
        logger.debug(f'Could not process date {x}')

    return x


class ReviewItem(scrapy.Item):
    product_id = scrapy.Field()
    page = scrapy.Field()
    page_order = scrapy.Field()
    recommended = scrapy.Field(
        output_processor=Compose(TakeFirst(), simplify_recommended),
    )
    date = scrapy.Field(
        output_processor=Compose(TakeFirst(), standardize_date)
    )
    text = scrapy.Field(
        input_processor=MapCompose(StripText()),
        output_processor=Compose(Join('\n'), StripText())
    )
    hours = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_float)
    )
    found_helpful = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    found_unhelpful = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    found_funny = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    compensation = scrapy.Field()
    username = scrapy.Field()
    user_id = scrapy.Field()
    products = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    early_access = scrapy.Field()
    
class ReviewItemLoader(ItemLoader):
    default_output_processor = TakeFirst()


def load_review(review, product_id, page, order):
    """
    Load a ReviewItem from a single review.
    """
    loader = ReviewItemLoader(ReviewItem(), review)

    loader.add_value('product_id', product_id)
    loader.add_value('page', page)
    loader.add_value('page_order', order)

    # Review data.
    loader.add_css('recommended', '.title::text')
    loader.add_css('date', '.date_posted::text', re='Posted: (.+)')
    loader.add_css('text', '.apphub_CardTextContent::text')
    loader.add_css('hours', '.hours::text', re='(.+) hrs')
    loader.add_css('compensation', '.received_compensation::text')

    # User/reviewer data.
    loader.add_css('user_id', '.apphub_CardContentAuthorName a::attr(href)', re='.*/profiles/(.+)/')
    loader.add_css('username', '.apphub_CardContentAuthorName a::text')
    loader.add_css('products', '.apphub_CardContentMoreLink ::text', re='([\d,]+) product')

    # Review feedback data.
    feedback = loader.get_css('.found_helpful ::text')
    loader.add_value('found_helpful', feedback, re='([\d,]+) of')
    loader.add_value('found_unhelpful', feedback, re='of ([\d,]+)')
    loader.add_value('found_funny', feedback, re='([\d,]+).*funny')

    early_access = loader.get_css('.early_access_review')
    if early_access:
        loader.add_value('early_access', True)
    else:
        loader.add_value('early_access', False)

    return loader.load_item()


def get_page(response):
    from_page = response.meta.get('from_page', None)

    if from_page:
        page = from_page + 1
    else:
        page = url_query_parameter(response.url, 'p', None)
        if page:
            page = str_to_int(page)

    return page


def get_product_id(response):
    product_id = response.meta.get('product_id', None)

    if not product_id:
        try:
            return re.findall("app/(.+?)/", response.url)[0]
        except:  
            return None
    else:
        return product_id

################################################################################################

class ReviewSpider(scrapy.Spider):
    name = 'reviews'
    start_urls = [
        # CS:GO
        'https://steamcommunity.com/app/730/reviews/?p=1&browsefilter=mostrecent',
    ]
    custom_settings = {
    'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1},
    'FEED_FORMAT':'json',                                 
    'FEED_URI': 'reviewresult.json'
    }

    def __init__(self, url_file=None, steam_id=730, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.url_file = url_file
        self.steam_id = 730

    def read_urls(self):
        with open(self.url_file, 'r') as f:
            for url in f:
                url = url.strip()
                if url:
                    yield scrapy.Request(url, callback=self.parse)

    def start_requests(self):
        if self.steam_id:
            url = (
                f'http://steamcommunity.com/app/{self.steam_id}/reviews/'
                '?browsefilter=mostrecent&p=1'
            )
            yield Request(url, callback=self.parse)
        elif self.url_file:
            yield from self.read_urls()
        else:
            for url in self.test_urls:
                yield Request(url, callback=self.parse)

    def parse(self, response):
        page = get_page(response)
        product_id = get_product_id(response)

        # Load all reviews on current page.
        reviews = response.css('div .apphub_Card')
        for i, review in enumerate(reviews):
            yield load_review(review, product_id, page, i)
            time.sleep(0.5)
            
        # Navigate to next page.
        form = response.xpath('//form[contains(@id, "MoreContentForm")]')
        if form:
            yield self.process_pagination_form(form, page, product_id)

    def process_pagination_form(self, form, page=None, product_id=None):
        action = form.xpath('@action').extract_first()
        names = form.xpath('input/@name').extract()
        values = form.xpath('input/@value').extract()

        formdata = dict(zip(names, values))
        meta = dict(prev_page=page, product_id=product_id)

        return FormRequest(
            url=action,
            method='GET',
            formdata=formdata,
            callback=self.parse,
            meta=meta
        )

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:60: ScrapyDeprecationWarning: scrapy.loader.processors.TakeFirst is deprecated, instantiate itemloaders.processors.TakeFirst instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:60: ScrapyDeprecationWarning: scrapy.loader.processors.Compose is deprecated, instantiate itemloaders.processors.Compose instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:63: ScrapyDeprecationWarning: scrapy.loader.processors.TakeFirst is deprecated, instantiate itemloaders.processors.TakeFirst instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:63: ScrapyDeprecationWarning: scrapy.loader.processors.Compose is deprecated, instantiate itemloaders.processors.Compose instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:66: ScrapyDeprecationWarning: scrapy.loader.processors.MapCompose is deprecated, instantiate itemloaders.processors.MapCompose instead.
/opt/anacon

In [6]:
from scrapy.crawler import CrawlerProcess

process = CrawlerProcess({
    'AUTOTHROTTLE_ENABLED': True,
    'DOWNLOADER_MIDDLEWARES': {
    'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware': None,
    'scrapy.downloadermiddlewares.retry.RetryMiddleware': None,
    'scrapy_fake_useragent.middleware.RandomUserAgentMiddleware': 400,
    'scrapy_fake_useragent.middleware.RetryUserAgentMiddleware': 401,
}
})

process.crawl(ReviewSpider)
process.start()

INFO:scrapy.utils.log:Scrapy 2.4.1 started (bot: scrapybot)
2021-01-13 18:22:34 [scrapy.utils.log] INFO: Scrapy 2.4.1 started (bot: scrapybot)
INFO:scrapy.utils.log:Versions: lxml 4.5.0.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.7.6 (default, Jan  8 2020, 13:42:34) - [Clang 4.0.1 (tags/RELEASE_401/final)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Darwin-19.5.0-x86_64-i386-64bit
2021-01-13 18:22:34 [scrapy.utils.log] INFO: Versions: lxml 4.5.0.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.7.6 (default, Jan  8 2020, 13:42:34) - [Clang 4.0.1 (tags/RELEASE_401/final)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Darwin-19.5.0-x86_64-i386-64bit
DEBUG:scrapy.utils.log:Using reactor: twisted.internet.selectreactor.SelectReactor
2021-01-13 18:22:34 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
INFO:scrapy

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/reviews/?browsefilter=mostrecent&p=1>
{'date': '13 January',
 'early_access': False,
 'hours': 10.7,
 'page': 1,
 'page_order': 1,
 'product_id': '730',
 'products': 12,
 'recommended': True,
 'text': 'its ok',
 'user_id': '76561198975062224',
 'username': 'Mitch McConnell'}
2021-01-13 18:22:40 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/reviews/?browsefilter=mostrecent&p=1>
{'date': '13 January',
 'early_access': False,
 'hours': 10.7,
 'page': 1,
 'page_order': 1,
 'product_id': '730',
 'products': 12,
 'recommended': True,
 'text': 'its ok',
 'user_id': '76561198975062224',
 'username': 'Mitch McConnell'}
DEBUG:__main__:Could not process date 13 January
2021-01-13 18:22:40 [__main__] DEBUG: Could not process date 13 January
DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/reviews/?browsefilter=mostrecent&p=1>
{'date': '13 January',
 'earl

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwvrb4%2FvYCfsvvwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videospage=2&artpage=2&allguidepage=2&webguidepage=2&integratedguidepage=2&discussionspage=2&numperpage=10&browsefilter=mostrecent&l=english&appHubSubSection=10&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-13',
 'early_access': False,
 'hours': 560.8,
 'page': 2,
 'page_order': 0,
 'product_id': '730',
 'products': 4,
 'recommended': True,
 'text': 'best game axaxa',
 'user_id': '76561198848592140',
 'username': '☠️トーマス☠️ CS.MONE'}
2021-01-13 18:22:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwvrb4%2FvYCfsvvwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videospage=2&artpage=2&all

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwvrb4%2FvYCfsvvwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videospage=2&artpage=2&allguidepage=2&webguidepage=2&integratedguidepage=2&discussionspage=2&numperpage=10&browsefilter=mostrecent&l=english&appHubSubSection=10&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-13',
 'early_access': False,
 'hours': 1795.3,
 'page': 2,
 'page_order': 6,
 'product_id': '730',
 'products': 6,
 'recommended': True,
 'text': 'bestest (jw best))',
 'user_id': '76561198177045310',
 'username': 'kanon-'}
2021-01-13 18:22:49 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwvrb4%2FvYCfsvvwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videospage=2&artpage=2&allguidep

2021-01-13 18:22:52 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ4hbr2%2FvYCdbfvwgI%3D&userreviewsoffset=20&p=3&workshopitemspage=3&readytouseitemspage=3&mtxitemspage=3&itemspage=3&screenshotspage=3&videospage=3&artpage=3&allguidepage=3&webguidepage=3&integratedguidepage=3&discussionspage=3&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-13',
 'early_access': False,
 'hours': 375.3,
 'page': 3,
 'page_order': 0,
 'product_id': '730',
 'products': 3,
 'recommended': False,
 'text': 'yes',
 'user_id': '76561199094902358',
 'username': 'yes))'}
DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ4hbr2%2FvYCdbfvwgI%3D&userreviewsoffset=20&p=3&workshopitemspage=3&readytouseitemspage=3&mtxitemspage=3&itemspage=3&screenshotspage=3&videospage=3&artpage=3&allguidepage=3&

...

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm5HL8vYCcJbawQI%3D&userreviewsoffset=4850&p=486&workshopitemspage=486&readytouseitemspage=486&mtxitemspage=486&itemspage=486&screenshotspage=486&videospage=486&artpage=486&allguidepage=486&webguidepage=486&integratedguidepage=486&discussionspage=486&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-08',
 'early_access': False,
 'hours': 255.9,
 'page': 486,
 'page_order': 1,
 'product_id': '730',
 'products': 23,
 'recommended': True,
 'text': 'epic',
 'username': 'Abraham Lincoln'}
2021-01-13 19:11:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm5HL8vYCcJbawQI%3D&userreviewsoffset=4850&p=486&workshopitemspage=486&readytouseitemspage=486&mtxitemspage=486&itemspage=486&screenshotspage=486&videospage=486&artpage

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm5HL8vYCcJbawQI%3D&userreviewsoffset=4850&p=486&workshopitemspage=486&readytouseitemspage=486&mtxitemspage=486&itemspage=486&screenshotspage=486&videospage=486&artpage=486&allguidepage=486&webguidepage=486&integratedguidepage=486&discussionspage=486&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-08',
 'early_access': False,
 'hours': 262.5,
 'page': 486,
 'page_order': 7,
 'product_id': '730',
 'products': 6,
 'recommended': True,
 'text': 'headshot',
 'user_id': '76561198084373898',
 'username': 'Adolf'}
2021-01-13 19:11:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm5HL8vYCcJbawQI%3D&userreviewsoffset=4850&p=486&workshopitemspage=486&readytouseitemspage=486&mtxitemspage=486&itemspage=486&screenshotspage=

2021-01-13 19:11:08 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwqO%2FG8vYCdeLZwQI%3D&userreviewsoffset=4860&p=487&workshopitemspage=487&readytouseitemspage=487&mtxitemspage=487&itemspage=487&screenshotspage=487&videospage=487&artpage=487&allguidepage=487&webguidepage=487&integratedguidepage=487&discussionspage=487&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-08',
 'early_access': False,
 'hours': 247.4,
 'page': 487,
 'page_order': 1,
 'product_id': '730',
 'products': 2,
 'recommended': True,
 'text': 'Its nice',
 'username': 'V18E'}
DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwqO%2FG8vYCdeLZwQI%3D&userreviewsoffset=4860&p=487&workshopitemspage=487&readytouseitemspage=487&mtxitemspage=487&itemspage=487&screenshotspage=487&videospage=487&artpage=487

DEBUG:scrapy.core.scraper:Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwqO%2FG8vYCdeLZwQI%3D&userreviewsoffset=4860&p=487&workshopitemspage=487&readytouseitemspage=487&mtxitemspage=487&itemspage=487&screenshotspage=487&videospage=487&artpage=487&allguidepage=487&webguidepage=487&integratedguidepage=487&discussionspage=487&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-08',
 'early_access': False,
 'hours': 111.3,
 'page': 487,
 'page_order': 7,
 'product_id': '730',
 'products': 6,
 'recommended': True,
 'text': 'Nice shooter for clever and tactical players!',
 'user_id': '76561199112760845',
 'username': 'Parzival'}
2021-01-13 19:11:11 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwqO%2FG8vYCdeLZwQI%3D&userreviewsoffset=4860&p=487&workshopitemspage=487&readytouseitemspage=487&mtx

INFO:scrapy.core.engine:Spider closed (finished)
2021-01-13 19:11:17 [scrapy.core.engine] INFO: Spider closed (finished)


In [ ]:
import pandas as pd
df = pd.read_json('reviewresult.json')
df